In [1]:
import pandas as pd
import numpy as np
import scipy as sps
import plotly.graph_objs as go
from plotly.offline import init_notebook_mode, iplot #Ajouter plot pour enregistrer un html
from random import random

init_notebook_mode(connected=True)



traindata = pd.read_csv("input_train.csv", delimiter=",")
output = pd.read_csv("output_train.csv", delimiter=";")
input_test = pd.read_csv("input_test.csv", delimiter=",")
ID = input_test['ID']


In [2]:
np.random.seed(0)

In [3]:
dataAll = pd.concat((traindata, input_test), axis=0)

# Inutile ------------------------------------------------------------------------------------

dataAll[(dataAll['BUYER_BIRTHDAY_DATE']<1940) | (dataAll['BUYER_BIRTHDAY_DATE']>2000)] = np.nan
uniqueDates = dataAll['BUYER_BIRTHDAY_DATE'].value_counts()

freqs= np.cumsum(uniqueDates)
allval = freqs.iloc[-1]
freqs = freqs/allval

nbreNan = dataAll['BUYER_BIRTHDAY_DATE'].isnull().shape[0]

replace = [freqs.index.values[np.sum(random() > freqs)] for i in range(nbreNan)]

replacedf = pd.DataFrame({'BUYER_BIRTHDAY_DATE': replace})
dataAll.update(replacedf)

uniqueShippingMode = dataAll['SHIPPING_MODE'].value_counts()

freqs= np.cumsum(uniqueShippingMode)
allval = freqs.iloc[-1]
freqs = freqs/allval

nbreNan = dataAll['SHIPPING_MODE'].isnull().shape[0]

replace = [freqs.index.values[np.sum(random() > freqs)] for i in range(nbreNan)]

replacedf = pd.DataFrame(replace, columns=['SHIPPING_MODE'])
dataAll.update(replacedf)

# ------------------------------------------------------------------------------------------

In [4]:
dataAll['SHIPPING_MODE'] = dataAll['SHIPPING_MODE'].fillna('NORMAL')

dataAll['SHIPPING_PRICE'] = dataAll['SHIPPING_PRICE'].map({'<1': 0, '1<5':1, '5<10':2, '10<20':3, '>20': 4})
dataAll['SHIPPING_PRICE'] = dataAll['SHIPPING_PRICE'].fillna(0)

dataAll['WARRANTIES_PRICE'] = dataAll['WARRANTIES_PRICE'].map({'<5': 1, '5<20':2, '20<50':3, '50<100':4, '100<500':5})
dataAll['WARRANTIES_PRICE'] = dataAll['WARRANTIES_PRICE'].fillna(0)

dataAll['PRICECLUB_STATUS'] = dataAll['PRICECLUB_STATUS'].fillna("UNSUBSCRIBED")

dataAll['BUYER_BIRTHDAY_DATE'] = dataAll['BUYER_BIRTHDAY_DATE'].fillna(1977)
dataAll['BUYER_BIRTHDAY_DATE'][(dataAll['BUYER_BIRTHDAY_DATE']<1940) | (dataAll['BUYER_BIRTHDAY_DATE']>2000)] = 1977

dataAll['PURCHASE_COUNT'] = dataAll['PURCHASE_COUNT'].map({'<5':0, '5<20': 1, '20<50':2, '50<100':3, '100<500': 4, '>500':5})

dataAll['BUYING_DATE'] = dataAll['BUYING_DATE'].map({'1/2017':1, '2/2017':2,'3/2017':3,'4/2017':4,'5/2017':5, '6/2017':6, '7/2017':7, '8/2017':8, '9/2017':9, '10/2017':10})


dataAll['SELLER_SCORE_COUNT'] = dataAll['SELLER_SCORE_COUNT'].map({'<100':0, '100<1000':1, '1000<10000':2, '10000<100000':3, '100000<1000000':4})
dataAll['SELLER_SCORE_COUNT'] = dataAll['SELLER_SCORE_COUNT'].fillna(0)

dataAll['SELLER_SCORE_AVERAGE'] = dataAll['SELLER_SCORE_AVERAGE'].fillna(44)

dataAll['ITEM_PRICE'] = dataAll['ITEM_PRICE'].map({'<10':0, '10<20':1, '20<50':2, '50<100':3, '100<500':4, '500<1000':5, '1000<5000':6,'>5000':7})


/home/chems/.local/lib/python3.6/site-packages/ipykernel_launcher.py:12: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy



In [5]:
dataAll = pd.concat((dataAll, pd.get_dummies(dataAll['SHIPPING_MODE'], prefix="SHIPPING_MODE"),\
                 pd.get_dummies(dataAll['PRICECLUB_STATUS'], prefix="PRICECLUB_STATUS"),\
                 pd.get_dummies(dataAll['PRODUCT_FAMILY'], prefix="PRODUCT_FAMILY"),\
                 pd.get_dummies(dataAll['PRODUCT_TYPE'], prefix="PRODUCT_TYPE"),\
                 pd.get_dummies(dataAll['SELLER_COUNTRY'], prefix="SELLER_COUNTRY"),\
                 pd.get_dummies(dataAll['SELLER_DEPARTMENT'], prefix="SELLER_DEPARTMENT"),\
                 pd.get_dummies(dataAll['BUYER_DEPARTMENT'], prefix="BUYER_DEPARTMENT")), axis=1)

In [6]:
del dataAll['ID'], dataAll['SELLER_COUNTRY'], dataAll['SELLER_DEPARTMENT'], dataAll['BUYER_DEPARTMENT'],dataAll['PRODUCT_TYPE'], dataAll['SHIPPING_MODE'], dataAll['WARRANTIES_FLG'], dataAll['PRICECLUB_STATUS'], dataAll['PRODUCT_FAMILY']

In [7]:
train = dataAll.iloc[0:100000,0:]
test = dataAll.iloc[100000:,0:]

from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.metrics import accuracy_score
from sklearn.decomposition import PCA
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC

xtrain, xtest, ytrain, ytest = train_test_split(train, np.ravel(output['CLAIM_TYPE']))

In [8]:
#Trouver de nouvelles features avec une ACP
ACP = PCA()
ACP.fit(train)

d = [go.Scatter(y = np.cumsum(ACP.explained_variance_ratio_))]
iplot(d, filename='PCA Variances')


In [45]:

ACP = PCA(n_components = 4) #Voir le plot
ACP.fit(train)

Xtrans = ACP.transform(xtrain)
XtransT = ACP.transform(xtest)

cols=["ACP_{}".format(i) for i in range(ACP.n_components)]

#On créer les nouvelles variables
Xtrans = pd.DataFrame(Xtrans, columns=cols)
XtransT = pd.DataFrame(XtransT, columns=cols)

Xtrans.reset_index(drop=True, inplace=True)
xtrain.reset_index(drop=True,inplace=True)
XtransT.reset_index(drop=True, inplace=True)
xtest.reset_index(drop=True, inplace=True)

XtransTrain = pd.concat((xtrain, Xtrans), axis=1)
XtransTest = pd.concat((xtest, XtransT), axis=1)

In [10]:
classes = np.unique(output['CLAIM_TYPE'])

indices = [output['CLAIM_TYPE'] == classe for classe in classes]

print(["{}: {}".format(classes[i], i) for i in range(len(classes))])

['-: 0', 'DAMAGED: 1', 'DIFFERENT: 2', 'FAKE: 3', 'NOT_RECEIVED: 4', 'SELLER_CANCEL_POSTERIORI: 5', 'UNDEFINED: 6', 'WITHDRAWAL: 7']


In [44]:
classetrace0 = 0
classetrace1 = 2

trace0 = go.Scatter(
    x = Xtrans[indices[classetrace0]]['ACP_0'],
    y = Xtrans[indices[classetrace0]]['ACP_1'],
    name = classes[classetrace0],
    mode = 'markers',
    marker = dict(
        size = 5,
        color = 'red',
        line = dict(
            width = 0,
            color = 'rgb(0, 0, 0)'
        )
    )
)

trace1 = go.Scatter(
    x = Xtrans[indices[classetrace1]]['ACP_0'],
    y = Xtrans[indices[classetrace1]]['ACP_1'],
    name = classes[classetrace1],
    mode = 'markers',
    marker = dict(
        size = 5,
        color = 'blue',
        line = dict(
            width = 0,
        )
    )
)

iplot([trace0, trace1], filename='Plot ACP')

/home/chems/.local/lib/python3.6/site-packages/ipykernel_launcher.py:5: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/home/chems/.local/lib/python3.6/site-packages/ipykernel_launcher.py:6: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/home/chems/.local/lib/python3.6/site-packages/ipykernel_launcher.py:20: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/home/chems/.local/lib/python3.6/site-packages/ipykernel_launcher.py:21: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



In [46]:
#Regression Logistique sans ACP:
RL = LogisticRegression()
RL.fit(xtrain, ytrain)

predRL = RL.predict(xtest)

perfRL = accuracy_score(predRL, ytest)

print("RL sans les données de l'ACP:", perfRL)

RL sans les données de l'ACP: 0.523


In [46]:
#Regression Logistique avec ACP:
RLACP = LogisticRegression()
RLACP.fit(XtransTrain, ytrain)

predRLACP = RLACP.predict(XtransTest)
perfRLACP = accuracy_score(predRLACP, ytest)
print("RF sans les données de l'ACP:", perfRLACP)

RF sans les données de l'ACP: 0.52272


In [50]:
#RF sans ACP:
RF = RandomForestClassifier(n_estimators=100, random_state=0)
RF.fit(xtrain, ytrain)

predRF = RF.predict(xtest)
perfRF = accuracy_score(predRF, ytest)
print("RF sans les données de l'ACP:", perfRF)

RF sans les données de l'ACP: 0.56212


In [47]:
#RF avec ACP
RFACP = RandomForestClassifier(n_estimators=100, random_state=0)
RFACP.fit(XtransTrain, ytrain)

predRFACP = RFACP.predict(XtransTest)
perfRFACP = accuracy_score(predRFACP, ytest)
print("RF avec les données de l'ACP:", perfRFACP)

RF avec les données de l'ACP: 0.56248


In [12]:
nclasses = len(classes)
estimateurs = np.zeros((nclasses,nclasses), dtype=object)

In [81]:
classes = list(classes)

In [82]:
#DDAG avec logistique
for i in range(nclasses):
    for j in range(i):
        A = classes[i]
        B = classes[j]
        
        indices = (ytrain == A) | (ytrain == B)
        
        estimateurs[i,j] = LogisticRegression()
        estimateurs[i,j].fit(xtrain[indices], ytrain[indices])

predictions = []
for ind, observ in xtest.iterrows():
    obs = observ.reshape(-1,419)
    classesAtest = classes[:]
    
    while len(classesAtest) > 1:
       
        A = classesAtest[-1]
        B = classesAtest[0]
        
        indexA = classes.index(A)
        indexB = classes.index(B)
        
        pred = estimateurs[indexA, indexB].predict(obs)
        
        
        if pred == A:
            classesAtest.remove(B)
        else:
            classesAtest.remove(A)
    print("index {} traîté".format(ind))
    predictions.append(classesAtest[0])
predictions = pd.DataFrame(predictions, columns=['CLAIM_TYPE'])

print("DDAG avec regressions logistiques: {}".format(accuracy_score(predictions,ytest)))

In [88]:
accuracy_score(predictions,ytest)

0.52504

In [89]:
#DDAG avec RF
for i in range(nclasses):
    for j in range(i):
        A = classes[i]
        B = classes[j]
        
        indices = (ytrain == A) | (ytrain == B)
        
        estimateurs[i,j] = RandomForestClassifier(n_estimators=100, random_state=0)
        estimateurs[i,j].fit(xtrain[indices], ytrain[indices])

predictions = []
for ind, observ in xtest.iterrows():
    obs = observ.reshape(-1,419)
    classesAtest = classes[:]
    
    while len(classesAtest) > 1:
       
        A = classesAtest[-1]
        B = classesAtest[0]
        
        indexA = classes.index(A)
        indexB = classes.index(B)
        
        pred = estimateurs[indexA, indexB].predict(obs)
        
        
        if pred == A:
            classesAtest.remove(B)
        else:
            classesAtest.remove(A)
    print("index {} traîté".format(ind))
    predictions.append(classesAtest[0])
predictions = pd.DataFrame(predictions, columns=['CLAIM_TYPE'])

print("DDAG avec RF: {}".format(accuracy_score(predictions,ytest))) #0.56328

/home/chems/.local/lib/python3.6/site-packages/ipykernel_launcher.py:13: FutureWarning:

reshape is deprecated and will raise in a subsequent release. Please use .values.reshape(...) instead



index 10655 traîté
index 29762 traîté
index 63784 traîté
index 10594 traîté
index 20934 traîté
index 22540 traîté
index 38438 traîté
index 4988 traîté
index 17380 traîté
index 97537 traîté
index 51037 traîté
index 71904 traîté
index 74646 traîté
index 90518 traîté
index 7521 traîté
index 35663 traîté
index 77953 traîté
index 56735 traîté
index 60462 traîté
index 50362 traîté
index 70538 traîté
index 40572 traîté
index 79069 traîté
index 84839 traîté
index 16925 traîté
index 2373 traîté
index 37187 traîté
index 978 traîté
index 6045 traîté
index 72755 traîté
index 75050 traîté
index 81349 traîté
index 85076 traîté
index 9657 traîté
index 23271 traîté
index 71384 traîté
index 69700 traîté
index 21752 traîté
index 23718 traîté
index 8216 traîté
index 54042 traîté
index 46964 traîté
index 92471 traîté
index 91443 traîté
index 37284 traîté
index 62167 traîté
index 40453 traîté
index 8559 traîté
index 58292 traîté
index 37708 traîté
index 70014 traîté
index 1647 traîté
index 90879 traîté
ind

index 40918 traîté
index 67955 traîté
index 90099 traîté
index 88630 traîté
index 2827 traîté
index 75681 traîté
index 56910 traîté
index 51357 traîté
index 26934 traîté
index 26494 traîté
index 7428 traîté
index 89790 traîté
index 47789 traîté
index 87435 traîté
index 47809 traîté
index 66573 traîté
index 9412 traîté
index 42685 traîté
index 93544 traîté
index 40679 traîté
index 75693 traîté
index 65921 traîté
index 88457 traîté
index 54773 traîté
index 54746 traîté
index 62435 traîté
index 33163 traîté
index 75847 traîté
index 61912 traîté
index 43424 traîté
index 25182 traîté
index 12239 traîté
index 41980 traîté
index 23870 traîté
index 99207 traîté
index 28347 traîté
index 86246 traîté
index 94776 traîté
index 14793 traîté
index 51225 traîté
index 91131 traîté
index 87535 traîté
index 95525 traîté
index 57970 traîté
index 34740 traîté
index 79324 traîté
index 75403 traîté
index 7232 traîté
index 5284 traîté
index 87187 traîté
index 42577 traîté
index 35198 traîté
index 21207 traît

index 99575 traîté
index 43233 traîté
index 4007 traîté
index 95979 traîté
index 55236 traîté
index 9451 traîté
index 56618 traîté
index 61268 traîté
index 38020 traîté
index 34220 traîté
index 57505 traîté
index 51808 traîté
index 53458 traîté
index 22040 traîté
index 12374 traîté
index 40340 traîté
index 44886 traîté
index 1035 traîté
index 40222 traîté
index 16146 traîté
index 12131 traîté
index 64735 traîté
index 54863 traîté
index 85118 traîté
index 78648 traîté
index 87025 traîté
index 97095 traîté
index 4913 traîté
index 62353 traîté
index 39538 traîté
index 74214 traîté
index 2490 traîté
index 99307 traîté
index 74170 traîté
index 25833 traîté
index 30008 traîté
index 25085 traîté
index 80564 traîté
index 61348 traîté
index 53398 traîté
index 85066 traîté
index 35638 traîté
index 25159 traîté
index 57090 traîté
index 95642 traîté
index 70614 traîté
index 85284 traîté
index 2107 traîté
index 87861 traîté
index 77949 traîté
index 7568 traîté
index 16112 traîté
index 77587 traîté


index 13869 traîté
index 77643 traîté
index 58989 traîté
index 73966 traîté
index 95131 traîté
index 56892 traîté
index 38289 traîté
index 22797 traîté
index 66513 traîté
index 48138 traîté
index 29273 traîté
index 10077 traîté
index 28859 traîté
index 34090 traîté
index 162 traîté
index 50375 traîté
index 1159 traîté
index 67944 traîté
index 89598 traîté
index 22794 traîté
index 50772 traîté
index 54818 traîté
index 84733 traîté
index 59800 traîté
index 75191 traîté
index 3502 traîté
index 63209 traîté
index 54108 traîté
index 22599 traîté
index 90036 traîté
index 97020 traîté
index 74715 traîté
index 83860 traîté
index 58694 traîté
index 12022 traîté
index 15517 traîté
index 55040 traîté
index 63555 traîté
index 27477 traîté
index 46388 traîté
index 74781 traîté
index 74597 traîté
index 15712 traîté
index 5027 traîté
index 88450 traîté
index 48480 traîté
index 40430 traîté
index 41759 traîté
index 76901 traîté
index 62509 traîté
index 72608 traîté
index 98519 traîté
index 55615 traît

...

index 30761 traîté
index 11691 traîté
index 19456 traîté
index 89151 traîté
index 38337 traîté
index 82450 traîté
index 52729 traîté
index 99438 traîté
index 25727 traîté
index 1644 traîté
index 31216 traîté
index 91595 traîté
index 99200 traîté
index 35531 traîté
index 36426 traîté
index 48757 traîté
index 97060 traîté
index 75527 traîté
index 21565 traîté
index 82162 traîté
index 32156 traîté
index 76666 traîté
index 36980 traîté
index 91763 traîté
index 82824 traîté
index 83954 traîté
index 90404 traîté
index 86106 traîté
index 8375 traîté
index 52844 traîté
index 42100 traîté
index 52459 traîté
index 8970 traîté
index 5579 traîté
index 86811 traîté
index 54453 traîté
index 77543 traîté
index 66459 traîté
index 67534 traîté
index 65158 traîté
index 31741 traîté
index 36603 traîté
index 81606 traîté
index 11803 traîté
index 87643 traîté
index 80683 traîté
index 4862 traîté
index 12024 traîté
index 52136 traîté
index 733 traîté
index 6718 traîté
index 45469 traîté
index 25863 traîté
i

index 73083 traîté
index 1873 traîté
index 50019 traîté
index 37653 traîté
index 15477 traîté
index 74582 traîté
index 61942 traîté
index 78292 traîté
index 66397 traîté
index 95229 traîté
index 47754 traîté
index 95160 traîté
index 41458 traîté
index 11072 traîté
index 4285 traîté
index 43094 traîté
index 52796 traîté
index 70849 traîté
index 12902 traîté
index 14984 traîté
index 46827 traîté
index 52529 traîté
index 73103 traîté
index 35511 traîté
index 74135 traîté
index 53719 traîté
index 18643 traîté
index 59963 traîté
index 43957 traîté
index 22838 traîté
index 97042 traîté
index 83305 traîté
index 4068 traîté
index 15182 traîté
index 56031 traîté
index 56753 traîté
index 16790 traîté
index 65433 traîté
index 82346 traîté
index 11967 traîté
index 64176 traîté
index 47784 traîté
index 89066 traîté
index 32643 traîté
index 68908 traîté
index 33069 traîté
index 59874 traîté
index 95541 traîté
index 70933 traîté
index 78236 traîté
index 61627 traîté
index 69819 traîté
index 91453 tra

index 64824 traîté
index 42598 traîté
index 62925 traîté
index 87080 traîté
index 49292 traîté
index 70783 traîté
index 55470 traîté
index 71818 traîté
index 3998 traîté
index 52314 traîté
index 36466 traîté
index 25234 traîté
index 94795 traîté
index 43003 traîté
index 63389 traîté
index 56680 traîté
index 76582 traîté
index 27033 traîté
index 58993 traîté
index 93962 traîté
index 731 traîté
index 45690 traîté
index 3481 traîté
index 9781 traîté
index 44400 traîté
index 59797 traîté
index 37709 traîté
index 96061 traîté
index 60494 traîté
index 20198 traîté
index 12935 traîté
index 61158 traîté
index 75057 traîté
index 98799 traîté
index 70746 traîté
index 25172 traîté
index 80113 traîté
index 57416 traîté
index 9770 traîté
index 44463 traîté
index 94349 traîté
index 31189 traîté
index 63761 traîté
index 21391 traîté
index 33427 traîté
index 69153 traîté
index 66570 traîté
index 66554 traîté
index 46310 traîté
index 52391 traîté
index 9436 traîté
index 30744 traîté
index 82493 traîté


index 89796 traîté
index 75671 traîté
index 76446 traîté
index 41018 traîté
index 36675 traîté
index 59590 traîté
index 66862 traîté
index 58204 traîté
index 48036 traîté
index 9699 traîté
index 30265 traîté
index 75456 traîté
index 35434 traîté
index 88963 traîté
index 58852 traîté
index 34085 traîté
index 11794 traîté
index 37893 traîté
index 89465 traîté
index 8815 traîté
index 72616 traîté
index 24489 traîté
index 39320 traîté
index 81478 traîté
index 81196 traîté
index 78218 traîté
index 17902 traîté
index 91234 traîté
index 45421 traîté
index 82177 traîté
index 89462 traîté
index 98103 traîté
index 34852 traîté
index 9485 traîté
index 2818 traîté
index 47980 traîté
index 59351 traîté
index 85769 traîté
index 12938 traîté
index 61635 traîté
index 51929 traîté
index 74271 traîté
index 55659 traîté
index 66068 traîté
index 14725 traîté
index 82158 traîté
index 44435 traîté
index 54463 traîté
index 25360 traîté
index 15916 traîté
index 48930 traîté
index 71131 traîté
index 70990 traî

index 1349 traîté
index 11831 traîté
index 77184 traîté
index 63499 traîté
index 52956 traîté
index 89767 traîté
index 93087 traîté
index 9125 traîté
index 31484 traîté
index 45108 traîté
index 41561 traîté
index 52411 traîté
index 53568 traîté
index 81871 traîté
index 39448 traîté
index 84714 traîté
index 8563 traîté
index 24337 traîté
index 42283 traîté
index 82583 traîté
index 23905 traîté
index 7961 traîté
index 9374 traîté
index 28329 traîté
index 19242 traîté
index 81153 traîté
index 27276 traîté
index 63009 traîté
index 25653 traîté
index 84327 traîté
index 95559 traîté
index 32347 traîté
index 9850 traîté
index 41378 traîté
index 94118 traîté
index 71868 traîté
index 13498 traîté
index 100 traîté
index 53123 traîté
index 32013 traîté
index 77500 traîté
index 96091 traîté
index 766 traîté
index 12927 traîté
index 56015 traîté
index 85162 traîté
index 77743 traîté
index 60361 traîté
index 89679 traîté
index 85710 traîté
index 44418 traîté
index 83934 traîté
index 50159 traîté
ind

In [ ]:
#DDAG SVM :  Pas encore lancé(lent chez moi)
for i in range(nclasses):
    for j in range(i):
        A = classes[i]
        B = classes[j]
        
        indices = (ytrain == A) | (ytrain == B)
        
        estimateurs[i,j] = SVC(class_weight='balanced')
        estimateurs[i,j].fit(xtrain[indices], ytrain[indices])

predictions = []
for ind, observ in xtest.iterrows():
    obs = observ.reshape(-1,419)
    classesAtest = classes[:]
    
    while len(classesAtest) > 1:
       
        A = classesAtest[-1]
        B = classesAtest[0]
        
        indexA = classes.index(A)
        indexB = classes.index(B)
        
        pred = estimateurs[indexA, indexB].predict(obs)
        
        
        if pred == A:
            classesAtest.remove(B)
        else:
            classesAtest.remove(A)
    print("index {} traîté".format(ind))
    predictions.append(classesAtest[0])
predictions = pd.DataFrame(predictions, columns=['CLAIM_TYPE'])

print("DDAG avec SVC: {}".format(accuracy_score(predictions,ytest)))

# Apres ça ne sert à rien

In [220]:
indicesBin = ytrain == '-'
ytrainBin = np.zeros(ytrain.shape, dtype='O')
ytrainBin[indicesBin] = '-'
ytrainBin[indicesBin != True] = 'ELSE'

indicesTest = ytest == '-'
ytestBin = np.zeros(ytest.shape, dtype='O')
ytestBin[indicesTest] = '-'
ytestBin[indicesTest != True] = 'ELSE'

In [212]:
RF = RandomForestClassifier(n_estimators=100, random_state=0)
RF.fit(xtrain, ytrainBin)

predRF = RF.predict(xtest)

In [218]:
print(accuracy_score(predRF, ytest))

0.3416


In [194]:
predRFproba = RF.predict_proba(xtest)[0:, 1]

ind = abs(predRFproba - 0.5) < 0.25

In [196]:
newxtest = xtest[ind]
newytestBin = ytest[ind]

indicesMulti = ytrain != '-'
indicesMultiTest = ytest != '-'

ytrainMulti = ytrain[indicesMulti]
xtrainMulti = xtrain[indicesMulti]

ytestMulti = ytest[indicesMultiTest]
xtestMulti = xtest[indicesMultiTest]


RFMulti = RandomForestClassifier(n_estimators=100, random_state=0)
RFMulti.fit(xtrainMulti, ytrainMulti)

RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=1,
            oob_score=False, random_state=0, verbose=0, warm_start=False)

In [197]:
predRF2 = RFMulti.predict(newxtest)

In [198]:
predRF[ind] = predRF2

In [202]:
accuracy_score(predRF, ytest)

0.24888

In [120]:
predRFproba[predRF != ytestBin].shape

(8348,)

In [121]:
predRFproba[predRF != ytestBin]

array([0.55, 0.28, 0.45, ..., 0.61, 0.23, 0.56])

In [110]:
predRF = RF.predict(xtest)
print(accuracy_score(ytestBin, predRF))

0.66608


In [99]:
df = pd.DataFrame(pred_test2, columns=['CLAIM_TYPE'])
df = pd.concat((ID, df), axis=1)

In [100]:
df.to_csv('output_test.csv', sep=';', columns=['ID', 'CLAIM_TYPE'], index=False) #Ecrire le fichier